<a href="https://colab.research.google.com/github/ArtyomMoiseev/urfu_profi_task1/blob/main/urfu_profi_solve.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Введение
Основная идея - выделить слова из текста с нужными метками после обработки текста библиотеками navec и slovnet.
## Выделение активных субъектов
После первичной обработки (лемматизации, разделения текста на токены) помечаем наши слова метками (obj, amod, apos и.т.д) с помощью библиотеки navec и slovonet, выделяем слова с нужными метками, в данном случае это: subj, obj, apos, nmod.
## Выделение сути событий.
Аналогично предыдущему пункту, только теперь выделяем слова с метками: advmod, root.
# Вывод
Получилось работоспособное решение. Конечно, вывод выглядит не слишком красиво, т.к не учитываются связи между словами, но если доработать этот момент, то это решение вполне можно использовать.
# Решение и пример:


In [61]:
!pip install navec
!pip install slovnet
!pip install ipymarkup
!pip install razdel
!wget https://storage.yandexcloud.net/natasha-slovnet/packs/slovnet_ner_news_v1.tar
!wget https://storage.yandexcloud.net/natasha-slovnet/packs/slovnet_syntax_news_v1.tar
!wget https://dovuz.urfu.ru/uploads/question_attachments/2022/03/10/6229a20db2ede.xlsx

--2022-03-11 08:30:56--  https://storage.yandexcloud.net/natasha-slovnet/packs/slovnet_ner_news_v1.tar
Resolving storage.yandexcloud.net (storage.yandexcloud.net)... 213.180.193.243, 2a02:6b8::1d9
Connecting to storage.yandexcloud.net (storage.yandexcloud.net)|213.180.193.243|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2385920 (2.3M) [application/octet-stream]
Saving to: ‘slovnet_ner_news_v1.tar.3’

slovnet_ner_news_v1 100%[===================>]   2.28M  2.42MB/s    in 0.9s    

2022-03-11 08:30:58 (2.42 MB/s) - ‘slovnet_ner_news_v1.tar.3’ saved [2385920/2385920]

--2022-03-11 08:30:58--  https://storage.yandexcloud.net/natasha-slovnet/packs/slovnet_syntax_news_v1.tar
Resolving storage.yandexcloud.net (storage.yandexcloud.net)... 213.180.193.243, 2a02:6b8::1d9
Connecting to storage.yandexcloud.net (storage.yandexcloud.net)|213.180.193.243|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2611200 (2.5M) [application/octet-stream]
Sav

In [63]:
from ipymarkup import show_dep_ascii_markup as show_markup
from razdel import sentenize, tokenize
from navec import Navec
from slovnet import Syntax
import pandas as pd
from navec import navec
import numpy as np
import nltk
from ipymarkup import show_span_ascii_markup as show_markup
navec = Navec.load('navec_news_v1_1B_250K_300d_100q.tar')
syntax = Syntax.load('slovnet_syntax_news_v1.tar')

In [64]:
df = pd.read_excel(r"6229a20db2ede.xlsx")
news_text = df["text"]

In [65]:
def work_with_text(text):
  chunk = []
  for sent in sentenize(text):
    tokens = [_.text for _ in tokenize(sent.text)]
    chunk.append(tokens)

  syntax.navec(navec)
  markup = next(syntax.map(chunk))

  words, deps = [], []
  for token in markup.tokens:
      words.append(token.text)
      deps.append(token.rel)

  req_objects = []
  think_objects = []

  for i in range(len(words)):
    if deps[i] == "subj" or deps[i] == "obj" or deps[i] == "amod" or deps[i] == "appos" or deps[i] == "nmod" or deps[i] == "flat:name":
      req_objects.append(words[i])
    if  deps[i] == "advmod" or deps[i] == "root" or deps[i] == "nsubj:pass":
      think_objects.append(words[i])
  print("text objects:")
  print(req_objects)
  print("Main text meaning:")
  print(" ".join(think_objects))
  return

In [66]:
for i in news_text:
  text = i.replace("'", "").replace('"', "").replace(".", "")
  print("text: " + i)
  work_with_text(text)

text:  Российская корпорация "Иркут" и египетский холдинг KATO Investment на авиасалоне в Дубае подписали ряд соглашений о развитии сотрудничества по проекту новейшего российского пассажирского самолета МС-21 . "В рамках программы сотрудничества заключено соглашение о закупке для авиакомпании Cairo Aviation (дочернее предприятие KATO Investment ) 6 самолетов МС-21. Соглашение также предусматривает опцион на 4 самолета МС-21" , — сообщается в понедельник на сайте российской компании. Кроме того, в настоящее время стороны обсуждают создание регионального центра по ремонту и обслуживанию МС-21 в районе международного аэропорта Аль-Аламейн, расположенного в 184 километрах от Каира. Египетская сторона планирует бесплатно предоставить площадь, примыкающую к воздушной гавани, для размещения производственных сооружений. Отметим, что в настоящее время на Иркутском авиазаводе ведется сборка первых летных прототипов МС-21. Первый полет запланирован на весну-лето будущего года, серийное производст